In [118]:
#main data file and import script for class group 6  project 1
# Author AO ottoaara@gmail.com. 952.693.1378 
# 5.5.23
# data source mpls open data https://opendata.minneapolismn.gov/datasets/cityoflakes::crime-data/explore?location=19.216823%2C-46.664577%2C4.00
# CSV option under Crime Data Header
import pandas as pd
import csv
import json
import matplotlib as pyplot
import geopandas as gpd
from shapely.geometry import Point, Polygon
import cartopy.crs as ccrs
import geoviews as gv #noqa
import pyproj
import hvplot.pandas

#crime_data_main  = full data set (75 Megs so seperated out into groups for ease of dev)
#ran_crime_data_df is a light 1000 rows of data randomly choosen from crime_data_man to work with
#crime_data_2019 = data for 2019 
#crime_data_2020 ...
#crime_data_2021 ...
#crime_data_2022...
##crime_data_2023 = data for 2023 
filename = "Crime_Data.csv"
csvdatapath = "Data/" + filename

In [119]:
# download local from repo to desktop (clone to your desktop)
#this reads the csv file 
crime_data_main = pd.read_csv(csvdatapath, encoding="utf-8")

In [120]:
crime_data_main2 = crime_data_main.head (100)
crime_data_main2

Unnamed: 0          X          Y                      Type Case_Number  \
0            0 -93.266383  44.967168  Additional Crime Metrics   19-004242   
1            1 -93.293230  45.033891  Additional Crime Metrics   19-011769   
2            2 -93.250318  44.968899  Additional Crime Metrics   19-013490   
3            3 -93.294961  45.018555  Additional Crime Metrics   19-026246   
4            4 -93.294961  45.018555  Additional Crime Metrics   19-026853   
..         ...        ...        ...                       ...         ...   
95          95 -93.274033  44.964585  Additional Crime Metrics   19-018994   
96          96 -93.218565  44.967887  Additional Crime Metrics   19-001533   
97          97 -93.301225  45.035447  Additional Crime Metrics   19-004892   
98          98 -93.268356  44.944983  Additional Crime Metrics   19-006510   
99          99 -93.288079  44.950999    Crime Offenses (NIBRS)   19-023382   

   Case_NumberAlt           Reported_Date           Occurred_Date  \
0      MP20194242  2019/01/05 02:50:00+00  2019/01/05 01:19:00+00   
1     MP201911769  2019/01/12 19:33:00+00  2019/01/12 17:40:00+00   
2     MP201913490  2019/01/14 20:23:00+00  2018/12/31 12:00:00+00   
3     MP201926246  2019/01/27 18:23:00+00  2019/01/26 00:15:00+00   
4     MP201926853  2019/01/28 17:45:00+00  2019/01/28 11:00:00+00   
..            ...                     ...                     ...   
95    MP201918994  2019/01/20 02:40:00+00  2019/01/19 23:38:00+00   
96     MP20191533  2019/01/02 14:55:00+00  2019/01/02 14:15:00+00   
97     MP20194892  2019/01/05 19:40:00+00  2019/01/05 19:40:00+00   
98     MP20196510  2019/01/07 16:26:00+00  2019/01/07 16:26:00+00   
99    MP201923382  2019/01/24 21:45:00+00  2019/01/24 17:20:00+00   

   NIBRS_Crime_Against     NIBRS_Group  ...                 Address Precinct  \
0       Non NIBRS Data  Non NIBRS Data  ...        0006XX 16TH ST E      1.0   
1       Non NIBRS Data  Non NIBRS Data  ...     0043XX DUPONT AVE N      4.0   
2       Non NIBRS Data  Non NIBRS Data  ...         0015XX 6TH ST S      1.0   
3       Non NIBRS Data  Non NIBRS Data  ...       0012XX 35TH AVE N      4.0   
4       Non NIBRS Data  Non NIBRS Data  ...       0012XX 35TH AVE N      4.0   
..                 ...             ...  ...                     ...      ...   
95      Non NIBRS Data  Non NIBRS Data  ...        0018XX 2ND AVE S      5.0   
96      Non NIBRS Data  Non NIBRS Data  ...  0001XX WILLIAMS AVE SE      2.0   
97      Non NIBRS Data  Non NIBRS Data  ...       0016XX 44TH AVE N      4.0   
98      Non NIBRS Data  Non NIBRS Data  ...        0005XX 32ND ST E      3.0   
99           Property          Group A  ...    0028XX LYNDALE AVE S      5.0   

                        Neighborhood  Ward  Latitude Longitude      wgsXAnon  \
0                        Elliot Park   6.0  44.96717 -93.26638 -1.038237e+07   
1                    Webber - Camden   4.0  45.03389 -93.29323 -1.038535e+07   
2                    Cedar Riverside   6.0  44.96890 -93.25032 -1.038058e+07   
3                            Folwell   4.0  45.01855 -93.29496 -1.038555e+07   
4                            Folwell   4.0  45.01855 -93.29496 -1.038555e+07   
..                               ...   ...       ...       ...           ...   
95  Steven's Square - Loring Heights   6.0  44.96459 -93.27403 -1.038322e+07   
96   Prospect Park - East River Road   2.0  44.96789 -93.21856 -1.037704e+07   
97                   Webber - Camden   4.0  45.03545 -93.30123 -1.038624e+07   
98                           Central   9.0  44.94498 -93.26836 -1.038259e+07   
99                          Whittier  10.0  44.95100 -93.28808 -1.038478e+07   

        wgsYAnon  Crime_Count  OBJECTID  
0   5.616354e+06            1         1  
1   5.626859e+06            1         2  
2   5.616627e+06            1         3  
3   5.624443e+06            1         4  
4   5.624443e+06            1         5  
..           ...          ...       ...  
95  5.615948e+06      

In [121]:
#columns listed for ease of co-development use. 
crime_data_main.columns

Index(['Unnamed: 0', 'X', 'Y', 'Type', 'Case_Number', 'Case_NumberAlt',
       'Reported_Date', 'Occurred_Date', 'NIBRS_Crime_Against', 'NIBRS_Group',
       'NIBRS_Code', 'Offense_Category', 'Offense', 'Problem_Initial',
       'Problem_Final', 'Address', 'Precinct', 'Neighborhood', 'Ward',
       'Latitude', 'Longitude', 'wgsXAnon', 'wgsYAnon', 'Crime_Count',
       'OBJECTID'],
      dtype='object')

In [122]:
#checkign data types 
crime_data_main.dtypes

Unnamed: 0               int64
X                      float64
Y                      float64
Type                    object
Case_Number             object
Case_NumberAlt          object
Reported_Date           object
Occurred_Date           object
NIBRS_Crime_Against     object
NIBRS_Group             object
NIBRS_Code              object
Offense_Category        object
Offense                 object
Problem_Initial         object
Problem_Final           object
Address                 object
Precinct               float64
Neighborhood            object
Ward                   float64
Latitude               float64
Longitude              float64
wgsXAnon               float64
wgsYAnon               float64
Crime_Count              int64
OBJECTID                 int64
dtype: object

In [123]:
crime_data_main['Occurred_Date'] = pd.to_datetime(crime_data_main['Occurred_Date'])

In [124]:
#get count of one column to prep for null value check 
crime_data_main["X"].count()

226833

In [125]:
# Remove rows containing all null values- cleaning data set
crime_data_clean = crime_data_main.dropna(how='any')

In [126]:
# removing rows with null values.  
crime_data_clean["X"].count()

152154

In [127]:
# checking values of crime category to reduce our data set down further to violent crimes 
crime_data_clean["Offense_Category"].unique()

array(['Subset of NIBRS Assault Offenses', 'Drug/Narcotic Offenses ',
       'Burglary/Breaking & Entering ', 'Assault Offenses ',
       'Larceny/Theft Offenses ', 'Stolen Property Offenses ',
       'Fraud Offenses ', 'Animal Cruelty ', 'Motor Vehicle Theft ',
       'Sex Offenses ', 'Robbery ', 'Kidnapping/Abduction ',
       'Weapon Law Violations ', 'Embezzlement ',
       'Pornography/Obscene Material ', 'Subset of NIBRS Robbery',
       'Counterfeiting/Forgery ', 'Arson ', 'Prostitution Offenses ',
       'Destruction/Damage/Vandalism of Property ',
       'Extortion/Blackmail ', 'Homicide Offenses ', 'Human Trafficking ',
       'Bribery ', 'Gambling Offenses ', 'Gunshot Wound Victims',
       'Shots Fired Calls'], dtype=object)

In [128]:
# reducing the data sets to only have violent crimes in them.  Note Included motor vehicle theft due to the
# high volumme of car-jackings occuring in mpls. 

crime_categories = [
    #'Subset of NIBRS Assault Offenses',
    'Assault Offenses ',
    #'Larceny/Theft Offenses ',
    'Sex Offenses ',
    'Robbery ',
    #'Burglary/Breaking & Entering ',
    #'Motor Vehicle Theft ',
    #'Weapon Law Violations ',
    'Kidnapping/Abduction ',
    'Homicide Offenses ',
    'Human Trafficking ',
    'Gunshot Wound Victims ',
    #'Shots Fired Calls'
]

#crime_data_clean = crime_data_clean[crime_data_clean['Offense_Category'].isin(crime_categories)]


In [129]:
#changing Occured_Date filed to data/time from object
crime_data_clean['Occurred_Date'] = pd.to_datetime(crime_data_clean['Occurred_Date'])


/var/folders/58/l2xhf5w97cxgl7_mqf1_7hwh0000gn/T/ipykernel_33376/2250024751.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  crime_data_clean['Occurred_Date'] = pd.to_datetime(crime_data_clean['Occurred_Date'])


In [130]:
#checking to make sure date/time conv worked 
crime_data_clean.dtypes

Unnamed: 0                           int64
X                                  float64
Y                                  float64
Type                                object
Case_Number                         object
Case_NumberAlt                      object
Reported_Date                       object
Occurred_Date          datetime64[ns, UTC]
NIBRS_Crime_Against                 object
NIBRS_Group                         object
NIBRS_Code                          object
Offense_Category                    object
Offense                             object
Problem_Initial                     object
Problem_Final                       object
Address                             object
Precinct                           float64
Neighborhood                        object
Ward                               float64
Latitude                           float64
Longitude                          float64
wgsXAnon                           float64
wgsYAnon                           float64
Crime_Count

In [134]:
#building random data set 
n_samples = min(1000, len(crime_data_clean))
ran_crime_data_df = crime_data_clean.sample(n=n_samples, random_state=42)

In [135]:
crime_data_2019["Offense_Category"].unique()

array(['Subset of NIBRS Assault Offenses', 'Drug/Narcotic Offenses ',
       'Burglary/Breaking & Entering ', 'Assault Offenses ',
       'Stolen Property Offenses ', 'Larceny/Theft Offenses ',
       'Animal Cruelty ', 'Motor Vehicle Theft ', 'Robbery ',
       'Fraud Offenses ', 'Kidnapping/Abduction ', 'Sex Offenses ',
       'Weapon Law Violations ', 'Pornography/Obscene Material ',
       'Counterfeiting/Forgery ', 'Arson ',
       'Destruction/Damage/Vandalism of Property ', 'Embezzlement ',
       'Extortion/Blackmail ', 'Homicide Offenses ', 'Human Trafficking ',
       'Prostitution Offenses ', 'Bribery ', 'Gambling Offenses ',
       'Gunshot Wound Victims', 'Shots Fired Calls'], dtype=object)

In [166]:
#building year data sets
crime_data_2019 = crime_data_main[crime_data_main['Occurred_Date'].dt.year == 2019]
crime_data_2020 = crime_data_main[crime_data_main['Occurred_Date'].dt.year == 2020]
crime_data_2021 = crime_data_main[crime_data_main['Occurred_Date'].dt.year == 2021]
crime_data_2022 = crime_data_main[crime_data_main['Occurred_Date'].dt.year == 2022]
crime_data_2023 = crime_data_main[crime_data_main['Occurred_Date'].dt.year == 2023]

In [167]:
crime_data_2019 = crime_data_clean[crime_data_clean['Offense_Category'].isin(crime_categories)]
crime_data_2019["Offense_Category"].unique()

array(['Assault Offenses ', 'Sex Offenses ', 'Robbery ',
       'Kidnapping/Abduction ', 'Homicide Offenses ',
       'Human Trafficking '], dtype=object)

In [168]:
crime_data_2019.dtypes

Unnamed: 0                           int64
X                                  float64
Y                                  float64
Type                                object
Case_Number                         object
Case_NumberAlt                      object
Reported_Date                       object
Occurred_Date          datetime64[ns, UTC]
NIBRS_Crime_Against                 object
NIBRS_Group                         object
NIBRS_Code                          object
Offense_Category                    object
Offense                             object
Problem_Initial                     object
Problem_Final                       object
Address                             object
Precinct                           float64
Neighborhood                        object
Ward                               float64
Latitude                           float64
Longitude                          float64
wgsXAnon                           float64
wgsYAnon                           float64
Crime_Count

In [169]:
# grouping with smaller data set to look at where the crimes are happening - counting number of offenses 
#grouped_data = crime_data_clearn.groupby(['Neighborhood', 'Address']).size().reset_index(name='Offense_Count')
grouped_data = crime_data_clean.groupby(['Neighborhood', 'Address', 'Offense_Category']).size().reset_index(name='Offense_Count')


In [170]:
#sorting grouped data to show the worst parts of town ie sorting by places more than one offense occurred
sorted_grouped_data = grouped_data.sort_values(by='Offense_Count', ascending=False)


In [171]:
# viewing sorted data frame. 
sorted_grouped_data

Neighborhood                       Address  \
27722  Northeast Park      0014XX NEW BRIGHTON BLVD   
18710      Longfellow              0025XX LAKE ST E   
12545       Hawthorne          0021XX ALDRICH AVE N   
7196    Downtown West          0009XX NICOLLET MALL   
8519    East Phillips             0024XX 18TH AVE S   
...               ...                           ...   
18248    Linden Hills            0040XX QUEEN AVE S   
18247    Linden Hills      0040XX LINDEN HILLS BLVD   
18246    Linden Hills      0040XX LINDEN HILLS BLVD   
18245    Linden Hills      0040XX LINDEN HILLS BLVD   
41471     Windom Park  24TH AVE NE / FILLMORE ST NE   

                    Offense_Category  Offense_Count  
27722        Larceny/Theft Offenses             491  
18710        Larceny/Theft Offenses             362  
12545              Assault Offenses             347  
7196         Larceny/Theft Offenses             311  
8519               Assault Offenses             309  
...                              ...            ...  
18248              Assault Offenses               1  
18247           Motor Vehicle Theft               1  
18246        Larceny/Theft Offenses               1  
18245  Burglary/Breaking & Entering               1  
41471      Stolen Property Offenses               1  

[41472 rows x 4 columns]

In [172]:
# adding in date time to support further analysis to check correlation between time and offense
grouped_data_bydate = crime_data_clean.groupby(['Neighborhood', 'Address', 'Offense_Category', 'Occurred_Date']).size().reset_index(name='Offense_Count')


In [173]:
grouped_data_bydate

Neighborhood                       Address           Offense_Category  \
0          Armatage              0019XX 60TH ST W    Larceny/Theft Offenses    
1          Armatage              0020XX 60TH ST W       Motor Vehicle Theft    
2          Armatage              0021XX 53RD ST W          Assault Offenses    
3          Armatage              0021XX 53RD ST W          Assault Offenses    
4          Armatage              0021XX 53RD ST W          Assault Offenses    
...             ...                           ...                        ...   
150825  Windom Park    18HALF AVE NE / POLK ST NE       Motor Vehicle Theft    
150826  Windom Park  19TH AVE NE / GARFIELD ST NE       Motor Vehicle Theft    
150827  Windom Park   22ND AVE NE / ULYSSES ST NE       Motor Vehicle Theft    
150828  Windom Park  24TH AVE NE / FILLMORE ST NE    Larceny/Theft Offenses    
150829  Windom Park  24TH AVE NE / FILLMORE ST NE  Stolen Property Offenses    

                   Occurred_Date  Offense_Count  
0      2021-08-25 10:00:00+00:00              1  
1      2020-06-08 22:45:00+00:00              1  
2      2019-06-29 19:00:00+00:00              1  
3      2019-07-08 15:29:00+00:00              1  
4      2020-06-25 00:00:00+00:00              1  
...                          ...            ...  
150825 2023-04-18 20:23:00+00:00              1  
150826 2023-01-04 23:00:00+00:00              1  
150827 2023-05-07 15:00:00+00:00              1  
150828 2023-03-24 22:27:00+00:00              1  
150829 2023-03-24 22:27:00+00:00              1  

[150830 rows x 5 columns]

In [174]:
# viewing sorted data frame. 
sorted_grouped_data = grouped_data_bydate.sort_values(by='Offense_Count', ascending=False)
sorted_grouped_data

Neighborhood                       Address  \
25024   Downtown West               0009XX 4TH ST S   
25019   Downtown West               0009XX 4TH ST S   
22954   Downtown West              0005XX 4TH AVE S   
53156         Holland            0007XX 23RD AVE NE   
8193          Central              0004XX LAKE ST E   
...               ...                           ...   
50515       Hawthorne             0028XX PACIFIC ST   
50516       Hawthorne             0028XX PACIFIC ST   
50517       Hawthorne             0028XX PACIFIC ST   
50518       Hawthorne             0028XX PACIFIC ST   
150829    Windom Park  24TH AVE NE / FILLMORE ST NE   

                                 Offense_Category             Occurred_Date  \
25024               Pornography/Obscene Material  2021-01-30 00:00:00+00:00   
25019               Pornography/Obscene Material  2020-01-30 00:00:00+00:00   
22954               Pornography/Obscene Material  2021-01-30 00:00:00+00:00   
53156   Destruction/Damage/Vandalism of Property  2023-02-22 01:00:00+00:00   
8193                                     Robbery  2020-05-28 00:05:00+00:00   
...                                           ...                       ...   
50515   Destruction/Damage/Vandalism of Property  2021-06-16 20:35:00+00:00   
50516   Destruction/Damage/Vandalism of Property  2022-09-16 16:00:00+00:00   
50517   Destruction/Damage/Vandalism of Property  2022-11-05 12:30:00+00:00   
50518                     Larceny/Theft Offenses  2023-02-03 08:00:00+00:00   
150829                  Stolen Property Offenses  2023-03-24 22:27:00+00:00   

        Offense_Count  
25024              37  
25019              26  
22954              18  
53156              11  
8193                9  
...               ...  
50515               1  
50516               1  
50517               1  
50518               1  
150829              1  

[150830 rows x 5 columns]

In [175]:
# adding long and lat. for analysis by location 
crime_data_byLongLat = grouped_data_bydate.merge(
    crime_data_clean[['Neighborhood', 'Address', 'Latitude', 'Longitude']],
    on=['Neighborhood', 'Address'],
    how='left')

In [176]:
crime_data_byLongLat

Neighborhood                       Address  \
0            Armatage              0019XX 60TH ST W   
1            Armatage              0020XX 60TH ST W   
2            Armatage              0021XX 53RD ST W   
3            Armatage              0021XX 53RD ST W   
4            Armatage              0021XX 53RD ST W   
...               ...                           ...   
20206857  Windom Park   22ND AVE NE / ULYSSES ST NE   
20206858  Windom Park  24TH AVE NE / FILLMORE ST NE   
20206859  Windom Park  24TH AVE NE / FILLMORE ST NE   
20206860  Windom Park  24TH AVE NE / FILLMORE ST NE   
20206861  Windom Park  24TH AVE NE / FILLMORE ST NE   

                   Offense_Category             Occurred_Date  Offense_Count  \
0           Larceny/Theft Offenses  2021-08-25 10:00:00+00:00              1   
1              Motor Vehicle Theft  2020-06-08 22:45:00+00:00              1   
2                 Assault Offenses  2019-06-29 19:00:00+00:00              1   
3                 Assault Offenses  2019-06-29 19:00:00+00:00              1   
4                 Assault Offenses  2019-06-29 19:00:00+00:00              1   
...                             ...                       ...            ...   
20206857       Motor Vehicle Theft  2023-05-07 15:00:00+00:00              1   
20206858    Larceny/Theft Offenses  2023-03-24 22:27:00+00:00              1   
20206859    Larceny/Theft Offenses  2023-03-24 22:27:00+00:00              1   
20206860  Stolen Property Offenses  2023-03-24 22:27:00+00:00              1   
20206861  Stolen Property Offenses  2023-03-24 22:27:00+00:00              1   

          Latitude  Longitude  
0         44.89430  -93.30421  
1         44.89431  -93.30545  
2         44.90693  -93.30675  
3         44.90693  -93.30675  
4         44.90693  -93.30675  
...            ...        ...  
20206857  45.00959  -93.23588  
20206858  45.01219  -93.24224  
20206859  45.01219  -93.24224  
20206860  45.01219  -93.24224  
20206861  45.01219  -93.24224  

[20206862 rows x 7 columns]

In [177]:
#display 2019 crime data
crime_data_2019["Type"].unique()

array(['Crime Offenses (NIBRS)'], dtype=object)

In [164]:
#Configure plot map for 2019
map_plot_2019 = crime_data_2019.hvplot.points(
    "Longitude",
    "Latitude",
    geo = True, 
    tiles = True, 
    frame_width = 800,
    frame_height = 600,
    c = "Offense_Category"
)

#Display the map plot
map_plot_2019


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]   (Offense_Category)

In [179]:
#Configure plot map for 2020
map_plot_2020 = crime_data_2020.hvplot.points(
    "Longitude",
    "Latitude",
    geo = True, 
    tiles = True, 
    frame_width = 800,
    frame_height = 600,
    c = "Offense_Category"
    
)

#Display the map plot
map_plot_2020

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]   (Offense_Category)

In [ ]:
#Configure plot map for 2021
map_plot_2021 = crime_data_2021.hvplot.points(
    "Longitude",
    "Latitude",
    geo = True, 
    tiles = True, 
    frame_width = 800,
    frame_height = 600,
    c = "Offense_Category"
)

#Display the map plot
map_plot_2021

In [ ]:
#Configure plot map for 2022
map_plot_2022 = crime_data_2022.hvplot.points(
    "Longitude",
    "Latitude",
    geo = True, 
    tiles = True, 
    frame_width = 800,
    frame_height = 600
)

#Display the map plot
map_plot_2022

In [ ]:
#Configure plot map for 2023
map_plot_2023 = crime_data_2023.hvplot.points(
    "Longitude",
    "Latitude",
    geo = True, 
    tiles = True, 
    frame_width = 800,
    frame_height = 600
)

#Display the map plot
map_plot_2023